# Исследование надёжности заёмщиков

Изучим данные, предоставленные сервисом для проекта.

## Шаг. Откройте файл с данными и изучите общую информацию

Импортируем библиотеку pandas. Прочитаем файл из папки /datasets/data.csv и сохраняем его в переменной data.

In [1]:
import pandas as pd #импортируем библиотеку для чтения файла

from pymystem3 import Mystem #импортируем библиотеку для лемматизации в шаге 2

from collections import Counter #импортируем Counter для подсчёта леммы в шаге 2

df = pd.read_csv('/datasets/data.csv')
df

children  days_employed  dob_years education  education_id  \
0             1   -8437.673028         42    высшее             0   
1             1   -4024.803754         36   среднее             1   
2             0   -5623.422610         33   Среднее             1   
3             3   -4124.747207         32   среднее             1   
4             0  340266.072047         53   среднее             1   
...         ...            ...        ...       ...           ...   
21520         1   -4529.316663         43   среднее             1   
21521         0  343937.404131         67   среднее             1   
21522         1   -2113.346888         38   среднее             1   
21523         3   -3112.481705         38   среднее             1   
21524         2   -1984.507589         40   среднее             1   

          family_status  family_status_id gender income_type  debt  \
0       женат / замужем                 0      F   сотрудник     0   
1       женат / замужем                 0      F   сотрудник     0   
2       женат / замужем                 0      M   сотрудник     0   
3       женат / замужем                 0      M   сотрудник     0   
4      гражданский брак                 1      F   пенсионер     0   
...                 ...               ...    ...         ...   ...   
21520  гражданский брак                 1      F   компаньон     0   
21521   женат / замужем                 0      F   пенсионер     0   
21522  гражданский брак                 1      M   сотрудник     1   
21523   женат / замужем                 0      M   сотрудник     1   
21524   женат / замужем                 0      F   сотрудник     0   

        total_income                       purpose  
0      253875.639453                 покупка жилья  
1      112080.014102       приобретение автомобиля  
2      145885.952297                 покупка жилья  
3      267628.550329    дополнительное образование  
4      158616.077870               сыграть свадьбу  
...              ...                           ...  
21520  224791.862382             операции с жильем  
21521  155999.806512          сделка с автомобилем  
21522   89672.561153                  недвижимость  
21523  244093.050500  на покупку своего автомобиля  
21524   82047.418899         на покупку автомобиля  

[21525 rows x 12 columns]

Одной командой получаем общую информацию о таблице.

In [2]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21525 entries, 0 to 21524
Data columns (total 12 columns):
children            21525 non-null int64
days_employed       19351 non-null float64
dob_years           21525 non-null int64
education           21525 non-null object
education_id        21525 non-null int64
family_status       21525 non-null object
family_status_id    21525 non-null int64
gender              21525 non-null object
income_type         21525 non-null object
debt                21525 non-null int64
total_income        19351 non-null float64
purpose             21525 non-null object
dtypes: float64(2), int64(5), object(5)
memory usage: 2.0+ MB


<div>
    <body>
По общей информации можно сказать следующее.
        
В таблице 12 столбцов. Типы данных в столбцах - <b>float64, int64</b> и <b>object</b>.
        
Согласно предоставленному описанию данных:<br />
        <b>children</b> — количество детей в семье;<br />
        <b>days_employed</b> — общий трудовой стаж в днях;<br />
        <b>dob_years</b> — возраст клиента в годах;<br />
        <b>education</b> — уровень образования клиента;<br />
        <b>education_id</b> — идентификатор уровня образования;<br />
        <b>family_status</b> — семейное положение;<br />
        <b>family_status_id</b> — идентификатор семейного положения;<br />
        <b>gender</b> — пол клиента;<br />
        <b>income_type</b> — тип занятости;<br />
        <b>debt</b> — имел ли задолженность по возврату кредитов;<br />
        <b>total_income</b> — ежемесячный доход;<br />
        <b>purpose</b> — цель получения кредита.<br />

В названиях колонок нарушения в стиле отсутствуют.<br />
Количество значений в столбцах различается - значит в данных есть пропущенные значения. Также стоит обратить внимание на столбцы days_employed и total_income, они представлены типом float64. Для дальнейшего анализа удобнее было бы работать с целочисленным типом данных. А ещё в столбце days_employed показались отрицательные значения, что очень смущает. Как же может быть отрицательным общий трудовой стаж..? Это скорее всего артефакт, что в реальной жизни часто встречается, как техническая ошибка при заполнении сотрдником банка анкеты о клиенте. Также, если посмотреть на таблицу, то сразу в третей строке видно, что образование с большой буквы написано, а остальные с маленькой. Значит есть неявные дубликаты в этом столбце.
    </body>
</div>

**Вывод**

Предварительно можно утверждать, что данных в таблице достаточно для проведения анализа, чтобы ответить на поставленные вопросы. Но так как встречаются пропуски в данных, вещественный тип, отрицательные значения и возможны дубликаты (явные и неявные), необходимо подготовить данные для дальнейшего анализа и провести предобработку данных.

## Шаг. Предобработка данных

### Обработка пропусков

Посичтаем сколько в таблице пропущенных значений. Для этого применим два метода pandas - <b>isna(), sum()</b>.

In [3]:
df.isna().sum()

children               0
days_employed       2174
dob_years              0
education              0
education_id           0
family_status          0
family_status_id       0
gender                 0
income_type            0
debt                   0
total_income        2174
purpose                0
dtype: int64

Обнаружились пропущенные зхначения в столбцах days_employed и total_income. Пропущенные зхначения не позволят работать с таблицей и провести качественный анализ данных. Но прежде чем приступить к обработке пропущенных значений, необходимо избавиться от артефактов - привести отрицательные значения в столбце days_employed в положительные. В реальной жизни такие значения могли появиться из-за технической ошибки сотрудника банка при заполнении анкеты клиента. Выполним замену отрицательных значений на положительные методом pandas abs().

In [4]:
df['days_employed'] = abs(df['days_employed']) #применяем метод abs()
df['days_employed'].unique() #смотрим уникальные значения столбца, чтобы убедиться что метод сработал

array([8437.67302776, 4024.80375385, 5623.42261023, ..., 2113.3468877 ,
       3112.4817052 , 1984.50758853])

Как видим отрицательных значений нет.

Теперь посмтотримм на пропущенные значения столбца total_income

In [5]:
df_total = df[df['total_income'].isna() == True][['children', 'dob_years', 'income_type', 'debt', 'total_income', 'purpose']]
df_total

children  dob_years  income_type  debt  total_income  \
12            0         65    пенсионер     0           NaN   
26            0         41  госслужащий     0           NaN   
29            0         63    пенсионер     0           NaN   
41            0         50  госслужащий     0           NaN   
55            0         54    пенсионер     1           NaN   
...         ...        ...          ...   ...           ...   
21489         2         47    компаньон     0           NaN   
21495         1         50    сотрудник     0           NaN   
21497         0         48    компаньон     0           NaN   
21502         1         42    сотрудник     0           NaN   
21510         2         28    сотрудник     0           NaN   

                                purpose  
12                      сыграть свадьбу  
26                          образование  
29     строительство жилой недвижимости  
41     сделка с подержанным автомобилем  
55                      сыграть свадьбу  
...                                 ...  
21489              сделка с автомобилем  
21495                           свадьба  
21497        строительство недвижимости  
21502  строительство жилой недвижимости  
21510           приобретение автомобиля  

[2174 rows x 6 columns]

Пропущенные значения находятся у людей в возрасте от 28 до 65 лет, и разных должностях. Сгруппируем новую таблицу по типу занятости с подсчетом значяений по каждой должности и посмотрим в каких должностях больше всего пропусков.

In [6]:
df_total.groupby('income_type')['income_type'].count().sort_values(ascending=False)

income_type
сотрудник          1105
компаньон           508
пенсионер           413
госслужащий         147
предприниматель       1
Name: income_type, dtype: int64

Получается что больше всего пропусков у сотрудников банка, далее компаньоны, пенсионеры, госслужащие и один предприниматель. Получается пять групп. Логично будет по этим группам сделать замену пропусков на среднее значение в каждой группе.

In [7]:
df['total_income'] = df['total_income'].fillna(df.groupby('income_type')['total_income'].transform('median'))

In [8]:
df.isna().sum() #проверяем пропуски в столбце total_income

children               0
days_employed       2174
dob_years              0
education              0
education_id           0
family_status          0
family_status_id       0
gender                 0
income_type            0
debt                   0
total_income           0
purpose                0
dtype: int64

Теперь остались пропуски в столбце days_employed. Общий трудовой стаж невозможно разграничить по группам, так как у каждого человека независимо от возраста он может быть разным. Для исследования значения общего трудового стажа не имеет особой важностию. Поэтому пропуски в этом столбце можно заменить применим медиану ко всему столбу сразу.

In [9]:
df['days_employed'] = df['days_employed'].median() #применяем метод медианы ко всему столбцу
df.isna().sum() #проверяем на наличие пропусков

children            0
days_employed       0
dob_years           0
education           0
education_id        0
family_status       0
family_status_id    0
gender              0
income_type         0
debt                0
total_income        0
purpose             0
dtype: int64

**Вывод**

Как видим в таблице пропущенные значения устранены. К каждому столбцу был применён свой метод обработки пропущенных значений.

### Замена типа данных

После замены пропусков выведем общую информацию на экран.

In [10]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21525 entries, 0 to 21524
Data columns (total 12 columns):
children            21525 non-null int64
days_employed       21525 non-null float64
dob_years           21525 non-null int64
education           21525 non-null object
education_id        21525 non-null int64
family_status       21525 non-null object
family_status_id    21525 non-null int64
gender              21525 non-null object
income_type         21525 non-null object
debt                21525 non-null int64
total_income        21525 non-null float64
purpose             21525 non-null object
dtypes: float64(2), int64(5), object(5)
memory usage: 2.0+ MB


Мы видем, что у total_income и days_employed тип данных float64. Для дальнейшего анализа необходимо перевести занчения столбцов total_income и days_employed в целочисленное. Последовательно применим метод .astype() к столбцам.

In [11]:
df['days_employed'] = df['days_employed'].astype('int')
df['total_income'] = df['total_income'].astype('int')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21525 entries, 0 to 21524
Data columns (total 12 columns):
children            21525 non-null int64
days_employed       21525 non-null int64
dob_years           21525 non-null int64
education           21525 non-null object
education_id        21525 non-null int64
family_status       21525 non-null object
family_status_id    21525 non-null int64
gender              21525 non-null object
income_type         21525 non-null object
debt                21525 non-null int64
total_income        21525 non-null int64
purpose             21525 non-null object
dtypes: int64(7), object(5)
memory usage: 2.0+ MB


**Вывод**

Как видим замена значений выполнена успешно. Можно приступить к устранению дубликатов.

### Обработка дубликатов

<div>
    <body>
Посчитаем явные дубликаты в таблице, применив методы <b>.duplicated()</b> и <b>.sum()</b> и удалим найденные дубликаты.
    </body>
</div>

In [12]:
df.duplicated().sum()

54

In [13]:
df = df.drop_duplicates().reset_index(drop=True) #удаляем явные дубликаты
df.duplicated().sum() #проверяем на наличие дубликатов

0

Когда изучали таблицу, мы увидели разные именования образования. Это неявные дубликаты. Найдём сначала их методом .unique(), а потом устраним их.

In [14]:
df['education'].unique() #ищем неявные дубликаты

array(['высшее', 'среднее', 'Среднее', 'СРЕДНЕЕ', 'ВЫСШЕЕ',
       'неоконченное высшее', 'начальное', 'Высшее',
       'НЕОКОНЧЕННОЕ ВЫСШЕЕ', 'Неоконченное высшее', 'НАЧАЛЬНОЕ',
       'Начальное', 'Ученая степень', 'УЧЕНАЯ СТЕПЕНЬ', 'ученая степень'],
      dtype=object)

Мы увидели какие показались разные именования в столбце education. Как видно у них одно общее - разный регистр. Устраним неявные дубликаты, приведём все к нижнему регистру применив .str.lower().

In [15]:
df['education'] = df['education'].str.lower()
df

children  days_employed  dob_years education  education_id  \
0             1           2194         42    высшее             0   
1             1           2194         36   среднее             1   
2             0           2194         33   среднее             1   
3             3           2194         32   среднее             1   
4             0           2194         53   среднее             1   
...         ...            ...        ...       ...           ...   
21466         1           2194         43   среднее             1   
21467         0           2194         67   среднее             1   
21468         1           2194         38   среднее             1   
21469         3           2194         38   среднее             1   
21470         2           2194         40   среднее             1   

          family_status  family_status_id gender income_type  debt  \
0       женат / замужем                 0      F   сотрудник     0   
1       женат / замужем                 0      F   сотрудник     0   
2       женат / замужем                 0      M   сотрудник     0   
3       женат / замужем                 0      M   сотрудник     0   
4      гражданский брак                 1      F   пенсионер     0   
...                 ...               ...    ...         ...   ...   
21466  гражданский брак                 1      F   компаньон     0   
21467   женат / замужем                 0      F   пенсионер     0   
21468  гражданский брак                 1      M   сотрудник     1   
21469   женат / замужем                 0      M   сотрудник     1   
21470   женат / замужем                 0      F   сотрудник     0   

       total_income                       purpose  
0            253875                 покупка жилья  
1            112080       приобретение автомобиля  
2            145885                 покупка жилья  
3            267628    дополнительное образование  
4            158616               сыграть свадьбу  
...             ...                           ...  
21466        224791             операции с жильем  
21467        155999          сделка с автомобилем  
21468         89672                  недвижимость  
21469        244093  на покупку своего автомобиля  
21470         82047         на покупку автомобиля  

[21471 rows x 12 columns]

In [16]:
df['education'].unique() #ищем неявные дубликаты

array(['высшее', 'среднее', 'неоконченное высшее', 'начальное',
       'ученая степень'], dtype=object)

Как видим, неявные дубликаты устранены.

**Вывод**

Посчитали и убрали из таблицы явные и неявные дубликаты.

### Лемматизация

Посмотрим на список лемм в столбце purpose

In [17]:
m = Mystem()

for x in df['purpose']:
    lemma = m.lemmatize(x)
    display(lemma)

['покупка', ' ', 'жилье', '\n']

['приобретение', ' ', 'автомобиль', '\n']

['покупка', ' ', 'жилье', '\n']

['дополнительный', ' ', 'образование', '\n']

['сыграть', ' ', 'свадьба', '\n']

...

['операция', ' ', 'с', ' ', 'жилье', '\n']

['сделка', ' ', 'с', ' ', 'автомобиль', '\n']

['недвижимость', '\n']

['на', ' ', 'покупка', ' ', 'свой', ' ', 'автомобиль', '\n']

['на', ' ', 'покупка', ' ', 'автомобиль', '\n']

Для того, чтобы обработать полученые значения, необходимо посмотреть на самые часто повторяющиеся леммы. Для этого сохраним униклаьные значения столбца и пройдёмся по нему циклом, чтрбы посчитать повторения лемм.

In [18]:
unique_purpose = df['purpose'].unique() #сохраняем уникальные значения

In [19]:
#цикл проходит по уникальным значеням и считает
lemmas_list = []
m = Mystem()

for purpose in unique_purpose:
    lemmas = ''.join(m.lemmatize(purpose)).strip()
    lemmas_list.append(lemmas)
print(Counter(lemmas_list))

Counter({'автомобиль': 2, 'покупка жилье': 1, 'приобретение автомобиль': 1, 'дополнительный образование': 1, 'сыграть свадьба': 1, 'операция с жилье': 1, 'образование': 1, 'на проведение свадьба': 1, 'покупка жилье для семья': 1, 'покупка недвижимость': 1, 'покупка коммерческий недвижимость': 1, 'покупка жилой недвижимость': 1, 'строительство собственный недвижимость': 1, 'недвижимость': 1, 'строительство недвижимость': 1, 'на покупка подержать автомобиль': 1, 'на покупка свой автомобиль': 1, 'операция с коммерческий недвижимость': 1, 'строительство жилой недвижимость': 1, 'жилье': 1, 'операция со свой недвижимость': 1, 'заниматься образование': 1, 'сделка с подержанный автомобиль': 1, 'получение образование': 1, 'свадьба': 1, 'получение дополнительный образование': 1, 'покупка свой жилье': 1, 'операция с недвижимость': 1, 'получение высокий образование': 1, 'свой автомобиль': 1, 'сделка с автомобиль': 1, 'профильный образование': 1, 'высокий образование': 1, 'покупка жилье для сдача':

Как видим часто повторяется автомобиль и недвижимость. Свадьба и образование достаточно реже. Подготовим данные для дальнейшей категоризации. Используя лемматизацию сразу сделаем категоризацию, и добавим новый столбец с выделленными категориями в датафрейм.

In [20]:
#сделаем через функцию, которая сразу переберёт леммы и раскидает их в соответствующие категории
def category_purpose(purpose):
    purpose = m.lemmatize(purpose)
    if ('жилье' in purpose or 'недвижимость' in purpose or 'жилой' in purpose):
        return 'недвижимость'
    elif 'автомобиль' in purpose:
        return 'автомобиль'
    elif  'свадьба' in purpose:
        return 'свадьба'
    else:
        return 'образование'
        
#добавим новый столбец в датафрейм, вызвав функцию
df['purpose_category'] = df['purpose'].apply(category_purpose)

In [21]:
df

children  days_employed  dob_years education  education_id  \
0             1           2194         42    высшее             0   
1             1           2194         36   среднее             1   
2             0           2194         33   среднее             1   
3             3           2194         32   среднее             1   
4             0           2194         53   среднее             1   
...         ...            ...        ...       ...           ...   
21466         1           2194         43   среднее             1   
21467         0           2194         67   среднее             1   
21468         1           2194         38   среднее             1   
21469         3           2194         38   среднее             1   
21470         2           2194         40   среднее             1   

          family_status  family_status_id gender income_type  debt  \
0       женат / замужем                 0      F   сотрудник     0   
1       женат / замужем                 0      F   сотрудник     0   
2       женат / замужем                 0      M   сотрудник     0   
3       женат / замужем                 0      M   сотрудник     0   
4      гражданский брак                 1      F   пенсионер     0   
...                 ...               ...    ...         ...   ...   
21466  гражданский брак                 1      F   компаньон     0   
21467   женат / замужем                 0      F   пенсионер     0   
21468  гражданский брак                 1      M   сотрудник     1   
21469   женат / замужем                 0      M   сотрудник     1   
21470   женат / замужем                 0      F   сотрудник     0   

       total_income                       purpose purpose_category  
0            253875                 покупка жилья     недвижимость  
1            112080       приобретение автомобиля       автомобиль  
2            145885                 покупка жилья     недвижимость  
3            267628    дополнительное образование      образование  
4            158616               сыграть свадьбу          свадьба  
...             ...                           ...              ...  
21466        224791             операции с жильем     недвижимость  
21467        155999          сделка с автомобилем       автомобиль  
21468         89672                  недвижимость     недвижимость  
21469        244093  на покупку своего автомобиля       автомобиль  
21470         82047         на покупку автомобиля       автомобиль  

[21471 rows x 13 columns]

In [22]:
df.isna().sum()

children            0
days_employed       0
dob_years           0
education           0
education_id        0
family_status       0
family_status_id    0
gender              0
income_type         0
debt                0
total_income        0
purpose             0
purpose_category    0
dtype: int64

**Вывод**

Мы подготовили данные для дальнейшей категоризации, столбец с новыми категориями добавлен в датафрейм успешно, пропусков нет.

### Категоризация данных

Начнём категоризировать данные с по очереди, подготавливая их для дальнейшего анализа и ответов на поставленные вопросы. 

In [23]:
#категоризируем по столбцу children
def category_children(kids):
    if kids['children'] != 0:
        return 'есть дети'
    else:
        return 'нет детей'
    
df['children_category'] = df.apply(category_children, axis=1)
df

children  days_employed  dob_years education  education_id  \
0             1           2194         42    высшее             0   
1             1           2194         36   среднее             1   
2             0           2194         33   среднее             1   
3             3           2194         32   среднее             1   
4             0           2194         53   среднее             1   
...         ...            ...        ...       ...           ...   
21466         1           2194         43   среднее             1   
21467         0           2194         67   среднее             1   
21468         1           2194         38   среднее             1   
21469         3           2194         38   среднее             1   
21470         2           2194         40   среднее             1   

          family_status  family_status_id gender income_type  debt  \
0       женат / замужем                 0      F   сотрудник     0   
1       женат / замужем                 0      F   сотрудник     0   
2       женат / замужем                 0      M   сотрудник     0   
3       женат / замужем                 0      M   сотрудник     0   
4      гражданский брак                 1      F   пенсионер     0   
...                 ...               ...    ...         ...   ...   
21466  гражданский брак                 1      F   компаньон     0   
21467   женат / замужем                 0      F   пенсионер     0   
21468  гражданский брак                 1      M   сотрудник     1   
21469   женат / замужем                 0      M   сотрудник     1   
21470   женат / замужем                 0      F   сотрудник     0   

       total_income                       purpose purpose_category  \
0            253875                 покупка жилья     недвижимость   
1            112080       приобретение автомобиля       автомобиль   
2            145885                 покупка жилья     недвижимость   
3            267628    дополнительное образование      образование   
4            158616               сыграть свадьбу          свадьба   
...             ...                           ...              ...   
21466        224791             операции с жильем     недвижимость   
21467        155999          сделка с автомобилем       автомобиль   
21468         89672                  недвижимость     недвижимость   
21469        244093  на покупку своего автомобиля       автомобиль   
21470         82047         на покупку автомобиля       автомобиль   

      children_category  
0             есть дети  
1             есть дети  
2             нет детей  
3             есть дети  
4             нет детей  
...                 ...  
21466         есть дети  
21467         нет детей  
21468         есть дети  
21469         есть дети  
21470         есть дети  

[21471 rows x 14 columns]

In [24]:
#категоризируем по столбцу задолженность
def debt_status(status):
    if status['debt'] != 0:
        return 'имел задолженность'
    else:
        return 'не имел задолженнности'
    
df['debt_status'] = df.apply(debt_status, axis=1)
df

children  days_employed  dob_years education  education_id  \
0             1           2194         42    высшее             0   
1             1           2194         36   среднее             1   
2             0           2194         33   среднее             1   
3             3           2194         32   среднее             1   
4             0           2194         53   среднее             1   
...         ...            ...        ...       ...           ...   
21466         1           2194         43   среднее             1   
21467         0           2194         67   среднее             1   
21468         1           2194         38   среднее             1   
21469         3           2194         38   среднее             1   
21470         2           2194         40   среднее             1   

          family_status  family_status_id gender income_type  debt  \
0       женат / замужем                 0      F   сотрудник     0   
1       женат / замужем                 0      F   сотрудник     0   
2       женат / замужем                 0      M   сотрудник     0   
3       женат / замужем                 0      M   сотрудник     0   
4      гражданский брак                 1      F   пенсионер     0   
...                 ...               ...    ...         ...   ...   
21466  гражданский брак                 1      F   компаньон     0   
21467   женат / замужем                 0      F   пенсионер     0   
21468  гражданский брак                 1      M   сотрудник     1   
21469   женат / замужем                 0      M   сотрудник     1   
21470   женат / замужем                 0      F   сотрудник     0   

       total_income                       purpose purpose_category  \
0            253875                 покупка жилья     недвижимость   
1            112080       приобретение автомобиля       автомобиль   
2            145885                 покупка жилья     недвижимость   
3            267628    дополнительное образование      образование   
4            158616               сыграть свадьбу          свадьба   
...             ...                           ...              ...   
21466        224791             операции с жильем     недвижимость   
21467        155999          сделка с автомобилем       автомобиль   
21468         89672                  недвижимость     недвижимость   
21469        244093  на покупку своего автомобиля       автомобиль   
21470         82047         на покупку автомобиля       автомобиль   

      children_category             debt_status  
0             есть дети  не имел задолженнности  
1             есть дети  не имел задолженнности  
2             нет детей  не имел задолженнности  
3             есть дети  не имел задолженнности  
4             нет детей  не имел задолженнности  
...                 ...                     ...  
21466         есть дети  не имел задолженнности  
21467         нет детей  не имел задолженнности  
21468         есть дети      имел задолженность  
21469         есть дети      имел задолженность  
21470         есть дети  не имел задолженнности  

[21471 rows x 15 columns]

Посмотрим на самое большое значение в столбце total_income, для того чтобы понять как разделить на группы весь столбец. Это необходимо делать, для дальнейшей оценки зависимости уровня дохода от возврата кредита. Поэтому удобнее всего это сделать  разделив столбец на три группы: низкий доход, средний дохзод и высокий доход.

In [25]:
df['total_income'].max() #выводим максимальное значение столбца

2265604

In [26]:
#категоризируем по столбцу total_income
def category_total_income(total):
    if total['total_income'] <= 750000:
        return 'низкий уровень дохода'
    elif (total['total_income'] > 750000)&(total['total_income'] <= 1500000):
        return 'средний уровень дохода'
    elif total['total_income'] > 1500000:
        return 'высокий уровень дохода'
    
df['total_income_category'] = df.apply(category_total_income, axis=1)
df #помотрим на датафрейм теперь, увидим новый столбец

children  days_employed  dob_years education  education_id  \
0             1           2194         42    высшее             0   
1             1           2194         36   среднее             1   
2             0           2194         33   среднее             1   
3             3           2194         32   среднее             1   
4             0           2194         53   среднее             1   
...         ...            ...        ...       ...           ...   
21466         1           2194         43   среднее             1   
21467         0           2194         67   среднее             1   
21468         1           2194         38   среднее             1   
21469         3           2194         38   среднее             1   
21470         2           2194         40   среднее             1   

          family_status  family_status_id gender income_type  debt  \
0       женат / замужем                 0      F   сотрудник     0   
1       женат / замужем                 0      F   сотрудник     0   
2       женат / замужем                 0      M   сотрудник     0   
3       женат / замужем                 0      M   сотрудник     0   
4      гражданский брак                 1      F   пенсионер     0   
...                 ...               ...    ...         ...   ...   
21466  гражданский брак                 1      F   компаньон     0   
21467   женат / замужем                 0      F   пенсионер     0   
21468  гражданский брак                 1      M   сотрудник     1   
21469   женат / замужем                 0      M   сотрудник     1   
21470   женат / замужем                 0      F   сотрудник     0   

       total_income                       purpose purpose_category  \
0            253875                 покупка жилья     недвижимость   
1            112080       приобретение автомобиля       автомобиль   
2            145885                 покупка жилья     недвижимость   
3            267628    дополнительное образование      образование   
4            158616               сыграть свадьбу          свадьба   
...             ...                           ...              ...   
21466        224791             операции с жильем     недвижимость   
21467        155999          сделка с автомобилем       автомобиль   
21468         89672                  недвижимость     недвижимость   
21469        244093  на покупку своего автомобиля       автомобиль   
21470         82047         на покупку автомобиля       автомобиль   

      children_category             debt_status  total_income_category  
0             есть дети  не имел задолженнности  низкий уровень дохода  
1             есть дети  не имел задолженнности  низкий уровень дохода  
2             нет детей  не имел задолженнности  низкий уровень дохода  
3             есть дети  не имел задолженнности  низкий уровень дохода  
4             нет детей  не имел задолженнности  низкий уровень дохода  
...                 ...                     ...                    ...  
21466         есть дети  не имел задолженнности  низкий уровень дохода  
21467         нет детей  не имел задолженнности  низкий уровень дохода  
21468         есть дети      имел задолженность  низкий уровень дохода  
21469         есть дети      имел задолженность  низкий уровень дохода  
21470         есть дети  не имел задолженнности  низкий уровень дохода  

[21471 rows x 16 columns]

In [27]:
df.isna().sum() #проверим ещё раз датафрейм на пропуски, прежде чем переходть к следующему разделу

children                 0
days_employed            0
dob_years                0
education                0
education_id             0
family_status            0
family_status_id         0
gender                   0
income_type              0
debt                     0
total_income             0
purpose                  0
purpose_category         0
children_category        0
debt_status              0
total_income_category    0
dtype: int64

**Вывод**

Теперь данные подготовлены. Мы категоризировали данные из датафрейма, чтобы было удобнее показать аналитику и ответить на вопросы. Также мы видим, что пропусков нет.

## Шаг. Ответьте на вопросы

Для того, чтобы ответить на все вопросы, будем для каждого вопроса создавать наглядную таблицу и делать выводы по посчитанно йдоли должников. Закономерно, что чем меньше процент, тем вероятность возврата кредита в срок возрастает.

- Есть ли зависимость между наличием детей и возвратом кредита в срок?

In [28]:
table_child = df.pivot_table(index = 'debt_status', columns = 'children_category', values = 'debt', aggfunc = 'count')

fmt = '{:.0%}'.format
table_child.loc['доля должников'] = (table_child.iloc[0] / table_child.iloc[1]).map(fmt)
display(table_child)

children_category      есть дети нет детей
debt_status                               
имел задолженность           678      1063
не имел задолженнности      6686     13044
доля должников               10%        8%

**Вывод**

Как видно из таблички, заёмщиков без детей по строке нет задолженности - больше всего. Такж и процент ниже, чем у заёмщиков с детьми. Значит можно утверждать, что отсутствие детей позвоялет заёмщикам возвращать кредит в срок.

- Есть ли зависимость между семейным положением и возвратом кредита в срок?

In [29]:
table_family = df.pivot_table(index = 'debt_status', columns = 'family_status', values = 'debt', aggfunc = 'count')

fmt = '{:.0%}'.format
table_family.loc['доля должников'] = (table_family.iloc[0] / table_family.iloc[1]).map(fmt)
display(table_family)

family_status          Не женат / не замужем в разводе вдовец / вдова  \
debt_status                                                             
имел задолженность                       274        85             63   
не имел задолженнности                  2536      1110            896   
доля должников                           11%        8%             7%   

family_status          гражданский брак женат / замужем  
debt_status                                              
имел задолженность                  388             931  
не имел задолженнности             3775           11413  
доля должников                      10%              8%

**Вывод**

В данной табличке мы видим, что больше всего не имеют задолженности клиенты зарегестрировавшие свой брак. При этом если смотреть на проценты, то самый низкий процент у овдовевших людей. Далее в равных процентах идут те, кто состоит в браке и те, кто развёлся. А самый большой процент у тех, кто не был в браке, ни в гражданском, ни в официальном. Получается, что семейное положение косвенно влияет на вероятность возврата кредита в срок. Люди состоящие в браке и те, кто прекратил брачные отношения (по собственной/не собственной воле) более дисциплинированы в выплатах по кредиту.

- Есть ли зависимость между уровнем дохода и возвратом кредита в срок?

In [30]:
table_total_income = df.pivot_table(index = 'debt_status', columns = 'total_income_category', values = 'debt', aggfunc = 'count')

fmt = '{:.0%}'.format
table_total_income.loc['доля должников'] = (table_total_income.iloc[0] / table_total_income.iloc[1]).map(fmt)
display(table_total_income)

total_income_category  высокий уровень дохода низкий уровень дохода  \
debt_status                                                           
имел задолженность                          1                  1737   
не имел задолженнности                      6                 19685   
доля должников                            17%                    9%   

total_income_category  средний уровень дохода  
debt_status                                    
имел задолженность                          3  
не имел задолженнности                     39  
доля должников                             8%

**Вывод**

Судя по табличке самое большое значение категории не имел задолженность у заёмщиков с низким уровнем дохода. Данная категория заёмщиков даже по процентам на втором месте. Самый низкий процент у заёмщиков со средним уровнем дохода. А с высоким уровнем дохода один из семи заёмщиков имел задолженность, что и сделало его процент большим. Здесь сложно говорить о влиянии уровня дохода на выплату кредита в срок. Этот один заёмщик из категории с высоким уровнем дохода возможно имел весомые причины по невыплате кредита. Да и к тому же по сравнению с другими заёмщиками, заёмщиков с высоким уровнем дохода мало. Поэтому сделать строгий вывод о зависимости между уровнем дохода и возвратом кредита в срок не возможно.

In [31]:
#код ревьюера
df['total_income_category'].value_counts()

низкий уровень дохода     21422
средний уровень дохода       42
высокий уровень дохода        7
Name: total_income_category, dtype: int64

- Как разные цели кредита влияют на его возврат в срок?

In [32]:
table_purpose = df.pivot_table(index = 'debt_status', columns = 'purpose_category', values = 'debt', aggfunc = 'count')

fmt = '{:.0%}'.format
table_purpose.loc['доля должников'] = (table_purpose.iloc[0] / table_purpose.iloc[1]).map(fmt)
display(table_purpose)

purpose_category       автомобиль недвижимость образование свадьба
debt_status                                                       
имел задолженность            403          782         370     186
не имел задолженнности       3905        10032        3644    2149
доля должников                10%           8%         10%      9%

**Вывод**

По всем параметрам заёмщики с целью кредита недвижимость дисциплинированно платят кредит. Действительно, кто бы хотел остаться без квартиры или иноного недвижимого имущества, от которого зависит твоя жизнь или работа, доход.

## Шаг. Общий вывод

Получается, что на возврат кредита в срок влияет отсутствие детей, семейное положение и цель кредита. Сделать строгий вывод о зависимости между уровнем дохода и возвратом кредита в срок не возможно.